### hundlekplatsen.se

In [1]:
import time
import datetime  
start_time = time.time()
start_str = datetime.datetime.now().strftime("%Y-%m-%d %H:%M")
print(f"Started: {start_str}")


Started: 2025-10-11 12:40


In [2]:
#!pip install playwright
#!playwright install

In [3]:
import asyncio
from playwright.async_api import async_playwright

BASE_URL = "https://www.hundlekplatsen.se/cities"

async def sniff_network(city):
    print(f"\n### Kollar {city} ###")
    async with async_playwright() as p:
        browser = await p.firefox.launch(headless=True)
        page = await browser.new_page()

        async def log_response(response):
            if response.request.resource_type == "xhr" or response.request.resource_type == "fetch":
                print(response.url)

        page.on("response", log_response)
        await page.goto(f"{BASE_URL}/{city}")
        await page.wait_for_load_state("networkidle")
        await asyncio.sleep(4)
        await browser.close()

await sniff_network("Stockholm")



### Kollar Stockholm ###
https://www.hundlekplatsen.se/?_rsc=yzu5s
https://www.hundlekplatsen.se/cities?_rsc=yzu5s
https://www.hundlekplatsen.se/dogpark/ChIJ3z3fAAB3X0YRvLUbrU0jIh4?_rsc=yzu5s
https://www.hundlekplatsen.se/dogpark/ChIJ_82puyR4X0YR-X20nxOS-2s?_rsc=yzu5s
https://www.hundlekplatsen.se/dogpark/ChIJjVFPtm93X0YRqyNMPxYEONY?_rsc=yzu5s
https://www.hundlekplatsen.se/dogpark/ChIJC34N_gd3X0YR95R_uUgldbQ?_rsc=yzu5s
https://www.hundlekplatsen.se/dogpark/ChIJHwFqtsN3X0YRbKyN8sXOt6s?_rsc=yzu5s
https://www.hundlekplatsen.se/dogpark/ChIJl7otMVV3X0YRk56h2JChk-U?_rsc=yzu5s


In [20]:
import asyncio
import json
import os
import time
from playwright.async_api import async_playwright

BASE_URL = "https://www.hundlekplatsen.se"
OUTPUT_FILE = "hundlekplatser_all.json"

# --- Helper to save progress ---
def save_progress(data):
    with open(OUTPUT_FILE, "w", encoding="utf-8") as f:
        json.dump(data, f, ensure_ascii=False, indent=2)
    print(f"💾 Progress saved ({len(data)} places)")

# --- Main scraping logic ---
async def get_city_links(page):
    """Collect all city links from /cities"""
    print("🌍 Fetching city list ...")
    await page.goto(f"{BASE_URL}/cities")
    await page.wait_for_load_state("networkidle")
    await asyncio.sleep(3)

    links = await page.query_selector_all("a[href*='/cities/']")
    cities = []
    for a in links:
        href = await a.get_attribute("href")
        name = (await a.inner_text()).strip()
        if href and href.startswith("/cities/"):
            cities.append({"name": name, "url": BASE_URL + href})
    print(f"✅ Found {len(cities)} cities.")
    return cities


async def get_places_for_city(page, city):
    """Find all dog parks in a given city"""
    print(f"🏙️ {city['name']}: loading page ...")
    await page.goto(city["url"])
    await page.wait_for_load_state("networkidle")
    await asyncio.sleep(3)

    cards = await page.query_selector_all("a[href*='/dogpark/']")
    places = []
    for c in cards:
        href = await c.get_attribute("href")
        name = (await c.inner_text()).strip()
        if href and href.startswith("/dogpark/"):
            places.append({
                "city": city["name"],
                "name": name,
                "url": f"{BASE_URL}{href}"
            })
    print(f"  ↳ Found {len(places)} dog parks")
    return places


async def get_place_details(page, place):
    """Open individual dog park and extract details"""
    await page.goto(place["url"])
    await page.wait_for_load_state("networkidle")
    await asyncio.sleep(2)

    desc_el = await page.query_selector("p, div.text-sm, div.text-base")
    desc = (await desc_el.inner_text()).strip() if desc_el else ""

    img_el = await page.query_selector("img")
    img = await img_el.get_attribute("src") if img_el else None
    if img and img.startswith("/"):
        img = BASE_URL + img

    place.update({
        "description": desc,
        "image": img
    })
    return place


async def main():
    # Load any existing progress
    if os.path.exists(OUTPUT_FILE):
        with open(OUTPUT_FILE, "r", encoding="utf-8") as f:
            all_places = json.load(f)
        print(f"🔁 Resuming from existing file with {len(all_places)} places")
    else:
        all_places = []

    processed_cities = {p["city"] for p in all_places}

    async with async_playwright() as p:
        browser = await p.firefox.launch(headless=True)
        page = await browser.new_page()

        # Step 1: collect all cities
        cities = await get_city_links(page)
        print(f"\n🚀 Starting scrape for {len(cities)} cities\n")

        # Step 2: go through cities
        for idx, city in enumerate(cities, 1):
            if city["name"] in processed_cities:
                print(f"⏭️ Skipping {city['name']} (already processed)")
                continue

            print(f"\n[{idx}/{len(cities)}] === {city['name']} ===")
            try:
                city_places = await get_places_for_city(page, city)
                for place in city_places:
                    try:
                        detailed = await get_place_details(page, place)
                        all_places.append(detailed)
                        print(f"  • {place['name']}")
                    except Exception as e:
                        print(f"⚠️ Error for {place['url']}: {e}")
                save_progress(all_places)
            except Exception as e:
                print(f"⚠️ Failed to fetch {city['name']}: {e}")
                save_progress(all_places)
                continue
            time.sleep(2)

        await browser.close()

    save_progress(all_places)
    print(f"\n🎉 Done! Collected {len(all_places)} places across Sweden")

import nest_asyncio
import asyncio

nest_asyncio.apply()
await main()


🌍 Fetching city list ...
✅ Found 354 cities.

🚀 Starting scrape for 354 cities


[1/354] === Abbekås
1 st ===
🏙️ Abbekås
1 st: loading page ...
  ↳ Found 1 dog parks
  • Hundrastplats
Rågångsvägen 10, 274 56 Abbekås, Sweden
💾 Progress saved (1 places)

[2/354] === Alingsås
2 st ===
🏙️ Alingsås
2 st: loading page ...
  ↳ Found 2 dog parks
  • Rullstolsanpassad ingång
Rullstolsanpassad parkering
Alingsås Hundkapplöpning
Mariedalsvägen 35, 441 41 Alingsås, Sweden
4.1
  • Hundrastgård Noltorp
441 56 Alingsås, Sweden
3.0
💾 Progress saved (3 places)

[3/354] === Almunge
1 st ===
🏙️ Almunge
1 st: loading page ...
  ↳ Found 1 dog parks
  • Picknickbord
Rullstolsanpassad parkering
Almunge Hundcenter
Almungeberg Vreta 41, 741 97 Almunge, Sweden
4.8
💾 Progress saved (4 places)

[4/354] === Alstad
1 st ===
🏙️ Alstad
1 st: loading page ...
  ↳ Found 1 dog parks
  • Hundrastgård
231 95 Alstad, Sweden
💾 Progress saved (5 places)

[5/354] === Anderslöv
1 st ===
🏙️ Anderslöv
1 st: loading page ...
  ↳ 

In [26]:
import json
import time
import urllib.parse
import folium
from geopy.geocoders import Nominatim

INPUT_FILE = "hundlekplatser_all.json"
OUTPUT_JSON = "hundlekplatser_sverige_geocoded.json"
OUTPUT_MAP = "hundlekplatser_sverige_map.html"

# --- Load data ---
with open(INPUT_FILE, "r", encoding="utf-8") as f:
    data = json.load(f)

geolocator = Nominatim(user_agent="hundlekplatsen_locator")

# --- Geocode missing coordinates ---
for i, place in enumerate(data, 1):
    if not place.get("latitude") or not place.get("longitude"):
        address = None

        # Try to find address in name or description
        parts = (place.get("name", "") + "\n" + place.get("description", "")).split("\n")
        for p in parts:
            if any(x in p.lower() for x in ["gatan", "väg", "stockholm", "sweden"]):
                address = p.strip()
                break
        if not address:
            address = f"{place.get('city','')}, Sweden"

        print(f"[{i}/{len(data)}] 🔍 Geocoding: {address}")
        try:
            loc = geolocator.geocode(address)
            if loc:
                place["latitude"], place["longitude"] = loc.latitude, loc.longitude
                print(f"✅ {place['name']} → ({loc.latitude:.5f}, {loc.longitude:.5f})")
            else:
                print(f"⚠️ No result for {address}")
        except Exception as e:
            print(f"⚠️ Error for {address}: {e}")
        time.sleep(1.1)  # Respect Nominatim rate limit

# --- Save updated JSON ---
with open(OUTPUT_JSON, "w", encoding="utf-8") as f:
    json.dump(data, f, ensure_ascii=False, indent=2)
print(f"\n💾 Saved updated data to {OUTPUT_JSON}")

# --- Create Folium map ---
m = folium.Map(location=[59.33, 18.07], zoom_start=6, tiles="OpenStreetMap")
fg = folium.FeatureGroup(name="Hundlekplatser")

for p in data:
    lat, lon = p.get("latitude"), p.get("longitude")
    if not lat or not lon:
        continue

    name = p.get("name", "Unknown place")
    desc = p.get("description", "")
    img = p.get("image")
    city = p.get("city", "")
    url = p.get("url")

    # Link to Hundlekplatsen or fallback search
    if not url:
        query = urllib.parse.quote(name)
        url = f"https://www.hundlekplatsen.se/search?q={query}"

    # Link to create OSM note
    osm_note_url = f"https://www.openstreetmap.org/note/new#map=18/{lat}/{lon}"

    popup_html = f"""
    <div style="font-size:14px;line-height:1.4">
      <b>{name}</b><br><i>{city}</i><br><br>
      {desc if desc else ''}
      <br><br>
      <a href="{url}" target="_blank">🐾 View on Hundlekplatsen.se</a><br>
      <a href="{osm_note_url}" target="_blank">✏️ Create OSM note</a>
      {'<br><br><img src="' + img + '" width="250">' if img else ''}
    </div>
    """

    folium.Marker(
        [lat, lon],
        popup=folium.Popup(popup_html, max_width=300),
        icon=folium.Icon(color="green", icon="paw", prefix="fa")
    ).add_to(fg)

fg.add_to(m)
folium.LayerControl().add_to(m)
m.save(OUTPUT_MAP)
print(f"🎉 Map created: {OUTPUT_MAP}")


[1/884] 🔍 Geocoding: Rågångsvägen 10, 274 56 Abbekås, Sweden
✅ Hundrastplats
Rågångsvägen 10, 274 56 Abbekås, Sweden → (55.39742, 13.59515)
[2/884] 🔍 Geocoding: Mariedalsvägen 35, 441 41 Alingsås, Sweden
✅ Rullstolsanpassad ingång
Rullstolsanpassad parkering
Alingsås Hundkapplöpning
Mariedalsvägen 35, 441 41 Alingsås, Sweden
4.1 → (57.91854, 12.52348)
[3/884] 🔍 Geocoding: 441 56 Alingsås, Sweden
✅ Hundrastgård Noltorp
441 56 Alingsås, Sweden
3.0 → (57.93929, 12.51289)
[4/884] 🔍 Geocoding: Almungeberg Vreta 41, 741 97 Almunge, Sweden
⚠️ No result for Almungeberg Vreta 41, 741 97 Almunge, Sweden
[5/884] 🔍 Geocoding: 231 95 Alstad, Sweden
✅ Hundrastgård
231 95 Alstad, Sweden → (55.45437, 13.20950)
[6/884] 🔍 Geocoding: Landsvägen 12, 231 70 Anderslöv, Sweden
✅ Hundrastgård Anderslöv
Landsvägen 12, 231 70 Anderslöv, Sweden → (55.43922, 13.31242)
[7/884] 🔍 Geocoding: S, Arboga, Sweden
✅ Arboga Hundbad
S, Arboga, Sweden
4.1 → (59.39655, 15.84518)
[8/884] 🔍 Geocoding: Hammartorpsvägen, 732 49 

In [27]:
m


In [31]:
import json
import folium
import urllib.parse

INPUT_FILE = "hundlekplatser_sverige_geocoded.json"
OUTPUT_MAP = "hundlekplatser_sverige_map.html"

# --- Läs in JSON ---
with open(INPUT_FILE, "r", encoding="utf-8") as f:
    data = json.load(f)

# --- Hjälpfunktion för färg och källa ---
def get_color_and_source(place):
    lat, lon = place.get("latitude"), place.get("longitude")
    if not lat or not lon:
        return "red", "Saknas"
    # Om platsen hade koordinater redan i originalet (dvs. från Hundlekplatsen)
    if place.get("url") and ("dogpark" in place["url"]):
        return "green", "Hundlekplatsen"
    # Annars om vi har fått dem via geokodning (t.ex. Nominatim)
    return "blue", "Nominatim"

# --- Skapa karta ---
m = folium.Map(location=[62.0, 15.0], zoom_start=5, tiles="CartoDB positron")
fg = folium.FeatureGroup(name="Hundlekplatser i Sverige")

for p in data:
    lat, lon = p.get("latitude"), p.get("longitude")
    if not lat or not lon:
        continue

    name = p.get("name", "Okänd plats").split("\n")[0]
    desc = p.get("description", "")
    city = p.get("city", "")
    img = p.get("image")
    url = p.get("url")
    if not url:
        query = urllib.parse.quote(name)
        url = f"https://www.hundlekplatsen.se/search?q={query}"

    osm_note_url = f"https://www.openstreetmap.org/note/new#map=18/{lat}/{lon}"

    color, source = get_color_and_source(p)

    popup_html = f"""
    <div style="font-size:14px; line-height:1.4">
      <b>{name}</b><br>
      <i>{city}</i><br><br>
      {desc if desc else ''}
      <br><br>
      <a href="{url}" target="_blank">🐾 Visa på Hundlekplatsen.se</a><br>
      <a href="{osm_note_url}" target="_blank">✏️ Skapa OSM-anteckning</a><br><br>
      {'<img src="' + img + '" width="250"><br>' if img else ''}
      <b>📍 Källa:</b> {source}
    </div>
    """

    folium.CircleMarker(
        location=[lat, lon],
        radius=5,
        color=color,
        fill=True,
        fill_color=color,
        fill_opacity=0.8,
        popup=folium.Popup(popup_html, max_width=300)
    ).add_to(fg)

fg.add_to(m)
folium.LayerControl().add_to(m)

# --- Spara karta ---
#m.save(OUTPUT_MAP)
print(f"🎨 Karta skapad: {OUTPUT_MAP}")
m


🎨 Karta skapad: hundlekplatser_sverige_map.html


In [32]:
import json

INPUT_FILE = "hundlekplatser_sverige_geocoded.json"
OUTPUT_FILE = "hundlekplatser_sverige.geojson"

# Läs JSON-data
with open(INPUT_FILE, "r", encoding="utf-8") as f:
    data = json.load(f)

features = []

for place in data:
    lat = place.get("latitude")
    lon = place.get("longitude")
    if not lat or not lon:
        continue  # hoppa över poster utan koordinater

    # Skapa GeoJSON feature
    feature = {
        "type": "Feature",
        "geometry": {
            "type": "Point",
            "coordinates": [lon, lat],
        },
        "properties": {
            "name": place.get("name"),
            "city": place.get("city"),
            "description": place.get("description"),
            "url": place.get("url"),
            "image": place.get("image"),
            # om du vill kan du lägga till fler attribut här
        }
    }
    features.append(feature)

geojson = {
    "type": "FeatureCollection",
    "features": features
}

# Spara GeoJSON-fil
with open(OUTPUT_FILE, "w", encoding="utf-8") as f:
    json.dump(geojson, f, ensure_ascii=False, indent=2)

print(f"🎉 Klar! Sparade {len(features)} punkter till {OUTPUT_FILE}")


🎉 Klar! Sparade 735 punkter till hundlekplatser_sverige.geojson


In [ ]:
import pandas as pd
import matplotlib.pyplot as plt

# --- Läs data ---


print("🔍 Totalt antal poster:", len(df))
print("Kolumner:", ", ".join(df.columns))

# --- Grundrensning ---
df["typ"] = df["typ"].fillna("Okänd")
df["adress"] = df["adress"].fillna("")

# --- Stat 1: Fördelning per typ ---
type_counts = df["typ"].value_counts().sort_values(ascending=False)
print("\n📊 Antal platser per typ:")
print(type_counts)

# --- Stat 2: Fördelning per stad (från adressfält) ---
df["stad"] = df["adress"].str.extract(r"([A-Za-zÅÄÖåäö\s\-]+)$")
city_counts = df["stad"].value_counts().head(10)
print("\n🏙️ Topp 10 städer:")
print(city_counts)

# --- Stat 3: Hur många har bilder? ---
df["har_bild"] = df["bilder"].apply(lambda x: isinstance(x, str) and len(x) > 5)
print(f"\n📸 Platser med bilder: {df['har_bild'].sum()} av {len(df)} ({df['har_bild'].mean()*100:.1f}%)")

# --- Plotta statistik ---
plt.figure(figsize=(7,5))
type_counts.plot(kind="bar", color="teal", alpha=0.8)
plt.title("Antal hundplatser per typ")
plt.xlabel("Typ av plats")
plt.ylabel("Antal")
plt.tight_layout()
plt.savefig("stat_typ.png")
plt.close()

plt.figure(figsize=(8,5))
city_counts.plot(kind="barh", color="orange", alpha=0.8)
plt.title("Topp 10 städer med flest hundplatser")
plt.xlabel("Antal platser")
plt.ylabel("Stad")
plt.tight_layout()
plt.savefig("stat_stad.png")
plt.close()

print("\n✅ Statistik sparad som:")
print("  - stat_typ.png (antal per typ)")
print("  - stat_stad.png (topp 10 städer)")

# --- Summeringsrapport ---
summary = {
    "Totalt antal platser": len(df),
    "Hundrastgårdar": int(type_counts.get("Hundrastgård", 0)),
    "Hundlekplatser": int(type_counts.get("Hundlekplats", 0)),
    "Hundbad": int(type_counts.get("Hundbad", 0)),
    "Okänd typ": int(type_counts.get("Okänd", 0)),
    "Platser med bilder": int(df["har_bild"].sum())
}

print("\n📈 Sammanfattning:")
for k, v in summary.items():
    print(f" - {k}: {v}")


In [ ]:
from datetime import datetime 
# End timer and calculate duration
end_time = time.time()
elapsed_time = end_time - start_time# Bygg audit-lager för den här etappen

# Print current date and total time
print("Date:", datetime.now().strftime("%Y-%m-%d %H:%M:%S"))
minutes, seconds = divmod(elapsed_time, 60)
print("Total time elapsed: {:02.0f} minutes {:05.2f} seconds".format(minutes, seconds))
